# Stakeholder Engagement - 05

In [5]:
# === 05) Stakeholder Engagement — generate strategies (Human-in-the-Loop) ===
# Requires: pandas, gradio, openai (OpenAI python client >= 1.0)

import os, re, json
from pathlib import Path
from datetime import datetime
import pandas as pd
import gradio as gr

# ---------- Project root + helpers ----------
def find_project_root(max_up=8):
    p = Path.cwd()
    for _ in range(max_up):
        if (p / "configs").exists() and ((p / "src").exists() or (p / "notebooks").exists()):
            return p
        p = p.parent
    return Path.cwd()

def slugify(s: str) -> str:
    return re.sub(r"[^0-9a-zA-Z]+", "-", (s or "").strip().lower()).strip("-") or "unknown"

ROOT = find_project_root()

# ---------- Load current state from run.yaml ----------
def get_current_state(default_state="kaduna"):
    try:
        import yaml
        run_yaml = yaml.safe_load((ROOT / "configs" / "run.yaml").read_text(encoding="utf-8"))
        st = run_yaml.get("current_state", default_state)
        return st
    except Exception:
        return default_state

# ---------- Resolve outputs dir (prefer "<slug>-state" if it exists) ----------
def outputs_dir_for_state(state: str) -> Path:
    slug = slugify(state)
    a = ROOT / "outputs" / f"{slug}-state"
    b = ROOT / "outputs" / slug
    if a.exists():
        return a
    if b.exists():
        return b
    a.mkdir(parents=True, exist_ok=True)
    return a

# ---------- Load latest pea_summaries.csv (context) ----------
def load_latest_pea():
    st = get_current_state()
    out_dir = outputs_dir_for_state(st)
    pea_csv = out_dir / "pea_summaries.csv"
    if not pea_csv.exists():
        # Fallback: empty context, still return dir so user can see clear error
        return {"subject":"","state":st,"issue":"","summary":""}, out_dir
    df = pd.read_csv(pea_csv)
    if "timestamp_utc" in df.columns and not df.empty:
        df = df.sort_values("timestamp_utc").tail(1)
    r = df.iloc[0].to_dict()
    return {
        "subject": r.get("subject",""),
        "state": r.get("state", st),
        "issue": r.get("issue_focus",""),
        "summary": r.get("summary",""),
    }, out_dir

# ---------- Load mapping CSV & ensure engagement_strategy column ----------
REQUIRED_COLS = ["stakeholder_type","entity","power","interest","threat","collab"]
ENGAGE_COL = "engagement_strategy"

def load_mapping(out_dir: Path):
    src = out_dir / "pea_stakeholder_scores_mapping.csv"
    if not src.exists():
        raise FileNotFoundError(
            f"Mapping file not found:\n{src}\n\n"
            "Please ensure Stakeholder Mapping saved 'pea_stakeholder_scores_mapping.csv' first."
        )
    df = pd.read_csv(src)
    # Basic sanity checks
    missing = [c for c in REQUIRED_COLS if c not in df.columns]
    if missing:
        raise ValueError(f"Mapping file is missing required columns: {missing}")
    if ENGAGE_COL not in df.columns:
        df[ENGAGE_COL] = ""  # add empty column for LLM to fill / user to edit
    # Keep a tidy, consistent column order (entity + abbr up front if present)
    col_order = []
    if "entity" in df.columns: col_order += ["entity"]
    if "abbr" in df.columns:   col_order += ["abbr"]
    col_order += [c for c in REQUIRED_COLS if c not in col_order]
    # tack on everything else (including engagement_strategy)
    for c in df.columns:
        if c not in col_order:
            col_order.append(c)
    df = df[col_order]
    return df, src

# ---------- OpenAI client (robust) ----------
def _load_openai_cfg():
    cfg_path = ROOT / "configs" / "config.json"
    cfg = {}
    if cfg_path.exists():
        try:
            cfg = json.loads(cfg_path.read_text(encoding="utf-8")) or {}
        except Exception:
            cfg = {}
    key = (
        os.getenv("OPENAI_API_KEY")
        or os.getenv("OPEN_API_KEY")
        or cfg.get("OPENAI_API_KEY")
        or cfg.get("OPEN_API_KEY")
    )
    base = os.getenv("OPENAI_BASE_URL") or cfg.get("ENVIRONMENT_URL") or cfg.get("OPENAI_BASE_URL")
    model = cfg.get("MODEL","gpt-4o-mini")
    return {"key": key, "base": base, "model": model}

def _openai_client_or_none():
    cfg = _load_openai_cfg()
    if not cfg["key"]:
        return None, cfg, "No OPENAI_API_KEY (or OPEN_API_KEY) found."
    try:
        from openai import OpenAI
        kwargs = {"api_key": cfg["key"]}
        if cfg["base"]:
            kwargs["base_url"] = cfg["base"]
        return OpenAI(**kwargs), cfg, None
    except Exception as e:
        return None, cfg, f"OpenAI init failed: {e}"

# ---------- LLM prompts (guard-railed) ----------
SYS_PROMPT = """You are a political-economy advisor. Your task is to craft *politically smart* engagement strategies for stakeholders.

Ethical & safety guardrails (MANDATORY):
- Do not include personal data about private individuals. Use only public roles/institutions.
- Avoid unverified allegations or defamatory language.
- Be specific but concise (1–3 sentences per strategy). No sensitive identifiers.
- Tailor advice to the local context and issue focus. If uncertain, give a cautious, general best-practice strategy.

Scoring semantics:
- power/interest/threat/collab are categorical in {Lo, Med, Hi}.
- Interpret as influence, attention, risk of obstruction, and coalition potential, respectively.

Return ONLY JSONL, one object per input row, with fields:
- entity
- engagement_strategy (1–3 sentences; concrete steps, partners, cadence, message framing)
"""

def build_user_prompt(context, rows_jsonl):
    subject = context.get("subject","")
    state   = context.get("state","")
    issue   = context.get("issue","")
    summary = context.get("summary","")

    return f"""Context:
Subject: {subject}
State: {state}
Issue Focus: {issue}

Background summary (for context only):
{summary}

Task:
For each stakeholder row below, produce an *Engagement Strategy* considering their power, interest, potential threat, and potential collaboration.
Prefer tangible actions: who to convene, messaging frames, cadence, incentives, coalition angles, accountability hooks.

Input rows (JSONL) with fields: stakeholder_type, entity, power, interest, threat, collab
{rows_jsonl}
"""

def llm_generate_strategies(context, df_in: pd.DataFrame) -> tuple[pd.DataFrame,str]:
    client, cfg, err = _openai_client_or_none()
    if client is None:
        return df_in, f"ℹ️ LLM unavailable: {err}"

    # Only send rows that have an entity name
    send = df_in[df_in["entity"].astype(str).str.strip() != ""].copy()
    if send.empty:
        return df_in, "ℹ️ No entities found to generate strategies for."

    # Build compact JSONL
    fields = ["stakeholder_type","entity","power","interest","threat","collab"]
    payload = []
    for _, r in send[fields].fillna("").iterrows():
        payload.append(json.dumps({k: r[k] for k in fields}, ensure_ascii=False))
    rows_jsonl = "\n".join(payload)

    try:
        resp = client.chat.completions.create(
            model=cfg["model"],
            temperature=0.2,
            messages=[
                {"role":"system", "content": SYS_PROMPT},
                {"role":"user",   "content": build_user_prompt(context, rows_jsonl)}
            ],
        )
        txt = (resp.choices[0].message.content or "").strip()
    except Exception as e:
        return df_in, f"⚠️ LLM call failed: {e}"

    # Parse JSONL and merge back by entity (case-insensitive)
    updates = {}
    for ln in txt.splitlines():
        ln = ln.strip()
        if not ln:
            continue
        ln = re.sub(r'^[\-\*\d\.\)\s]+', '', ln)  # be forgiving of bullets
        try:
            obj = json.loads(ln)
        except Exception:
            continue
        ent = str(obj.get("entity","")).strip()
        strat = str(obj.get("engagement_strategy","")).strip()
        if ent and strat:
            updates[ent.lower()] = strat

    if not updates:
        return df_in, "⚠️ LLM returned no usable strategies."

    out = df_in.copy()
    key_series = out["entity"].astype(str).str.strip().str.lower()
    filled = 0
    for i, k in enumerate(key_series):
        if k in updates:
            out.at[i, ENGAGE_COL] = updates[k]
            filled += 1
    return out, f"✅ Strategies generated for {filled} of {len(out)} rows."

# ---------- Save (overwrite + snapshot) ----------
def save_engagement(out_dir: Path, df: pd.DataFrame) -> str:
    dst = out_dir / "pea_stakeholder_scores_mapping_engage.csv"
    ts  = datetime.utcnow().isoformat(timespec="seconds").replace(":","-") + "Z"
    snap = out_dir / f"pea_stakeholder_scores_mapping_engage_{ts}.csv"
    df.to_csv(dst, index=False)
    df.to_csv(snap, index=False)
    return f"💾 Saved:\n- Latest: {dst}\n- Snapshot: {snap}"

# =========================
# Build Gradio UI
# =========================
context, OUT_DIR = load_latest_pea()
try:
    df_mapping, SRC_PATH = load_mapping(OUT_DIR)
    load_msg = f"Loaded mapping: `{SRC_PATH}` with {len(df_mapping)} rows."
except Exception as e:
    df_mapping = pd.DataFrame()
    load_msg = f"⚠️ Load failed: {e}"

with gr.Blocks(title="Stakeholder Engagement (Strategies)") as demo:
    gr.Markdown("## Stakeholder Engagement — Generate and Edit Strategies")

    # Read-only context (avoid user edits at this stage)
    with gr.Row():
        gr.Textbox(label="Subject", value=context.get("subject",""), interactive=False)
        gr.Textbox(label="State",   value=context.get("state",""),   interactive=False)
        gr.Textbox(label="Issue Focus", value=context.get("issue",""), interactive=False)

    gr.Markdown(load_msg)

    # Dataframe (editable so the user can refine strategies)
    table = gr.Dataframe(
        value=df_mapping,
        interactive=True,
        row_count=(min(10, max(1,len(df_mapping))), "dynamic"),
        label="Edit strategies here (only the 'engagement_strategy' column usually needs edits)."
    )

    with gr.Row():
        gen_btn  = gr.Button("Generate Strategies with LLM", variant="secondary")
        save_btn = gr.Button("Save Engagement CSV", variant="primary")

    status = gr.Markdown("")

    # --- Callbacks ---
    def _on_generate(df_current):
        # Ensure the required column exists (if user cleared it)
        df = pd.DataFrame(df_current)
        if ENGAGE_COL not in df.columns:
            df[ENGAGE_COL] = ""
        updated, msg = llm_generate_strategies(context, df)
        return updated, msg

    def _on_save(df_current):
        df = pd.DataFrame(df_current)
        if df.empty or df.get("entity","").astype(str).str.strip().eq("").all():
            return "⚠️ Nothing to save: no entities."
        # Minimal shape check
        miss = [c for c in REQUIRED_COLS if c not in df.columns]
        if miss:
            return f"⚠️ Missing required columns: {miss}"
        try:
            return save_engagement(OUT_DIR, df)
        except Exception as e:
            return f"⚠️ Save failed: {e}"

    gen_btn.click(_on_generate, inputs=[table], outputs=[table, status])
    save_btn.click(_on_save, inputs=[table], outputs=[status])

demo.launch(inline=True, share=False)

* Running on local URL:  http://127.0.0.1:7890
* To create a public link, set `share=True` in `launch()`.


/var/folders/gy/5jntfnt16t78c3dfbkhwnpcw0000gn/T/ipykernel_26690/3500996398.py:228: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  ts  = datetime.utcnow().isoformat(timespec="seconds").replace(":","-") + "Z"
